# 🔍 Building a NER Dataset From Scratch

This notebook is setup to annotate any provided dataset with defined labels, for training of named-entity recognition, a common NLP task.

We created this as part of our Ethical Spectacle Research [GUS-Net](https://ethicalspectacle.org/research-project?id=1) bias detection project, so it's setup to label sentences with Generalizations (GEN), Unfairness (UNFAIR), and Stereotypes (STEREO).

---



**Resources:** [🧪NER Model Demo](https://huggingface.co/spaces/maximuspowers/bias-detection-ner) | [🔬Model Repo](https://huggingface.co/maximuspowers/bias-detection-ner) | [💻Training Notebook](https://colab.research.google.com/drive/1TZBjpsJzRh5YvDGfSQn1MLsO3Z6etjj6#scrollTo=dgdlR1m9Zw-z) | [📝Blog Post]()

## 📡 Setup

1. Install Dependencies
2. Load Dataset to annotate
3. DSPy Config
4. Start UI to see LM calls

In [ ]:
#@title Install dependencies (restart runtime after)
!pip install transformers
# !pip install dspy-ai==2.1
!pip install dspy-ai
!pip install pymysql

!pip install 'arize-phoenix[evals]' # GUI
!pip install openinference-instrumentation-dspy # arize-phoenix uses this to interface to dspy tracing
!pip install opentelemetry-api
!pip install opentelemetry-sdk
!pip install opentelemetry-exporter-otlp

In [ ]:
#@title Load Training Dataset to Annotate
from datasets import load_dataset
import pandas as pd

dataset = load_dataset("mediabiasgroup/BABE", split="train") # using this as an example, but it's a good option
dataset = pd.DataFrame(dataset)
print("\n\nBABE:\n")
print(dataset.head())



BABE:

                                                text      outlet  label  \
0  NYPD Commissioner Dermot Shea on Monday expres...   Breitbart      0   
1  School systems across the country are adopting...  Federalist      1   
2  And then along came President Barry Obama, who...   Breitbart      1   
3  The curfews, which have never before occurred ...    Alternet      1   
4  Rather than help be a part of the solution, Tr...    Alternet      1   

               topic                                          news_link  \
0  marriage-equality  http://feedproxy.google.com/~r/breitbart/~3/F5...   
1              islam  https://thefederalist.com/2020/07/08/black-liv...   
2  marriage-equality  http://feedproxy.google.com/~r/breitbart/~3/ks...   
3     elections-2020  https://www.alternet.org/2020/06/we-just-got-a...   
4     elections-2020  https://www.alternet.org/2020/06/trump-thought...   

                                biased_words                    uuid  type  \
0          

In [ ]:
#@title DSPy Config / LLM
import dspy
import os
import openai

openai.api_key = 'sk-proj-nice-try' #@param

# model = dspy.HFModel(model='Qwen/Qwen2-7B-Instruct')
open_ai_model_endpoint = "gpt-4o" #@param
default_model = dspy.OpenAI(model=open_ai_model_endpoint, max_tokens=4096, model_type="chat", temperature=0.8)

dspy.settings.configure(lm=default_model, trace=[], temperature=0.8)
print("Language model configured successfully.")

Language model configured successfully.


In [ ]:
#@title Set Up Arize Phoenix UI

#@markdown This gives us an interface to explore each API call dspy makes (game changer). [Arize Phoenix Repo](https://github.com/Arize-ai/phoenix)

#########################################################################################################

# remember to:
# !pip install 'arize-phoenix[evals]' # GUI
# !pip install openinference-instrumentation-dspy # arize-phoenix uses this to interface to dspy tracing
# !pip install opentelemetry-api
# !pip install opentelemetry-sdk
# !pip install opentelemetry-exporter-otlp

# import libs
import phoenix as px
from openinference.instrumentation.dspy import DSPyInstrumentor
from opentelemetry import trace as trace_api
from opentelemetry.exporter.otlp.proto.http.trace_exporter import OTLPSpanExporter
from opentelemetry.sdk import trace as trace_sdk
from opentelemetry.sdk.trace.export import SimpleSpanProcessor

# launch ui
phoenix_session = px.launch_app()

# hook it up to dspy
endpoint = "http://127.0.0.1:6006/v1/traces"
tracer_provider = trace_sdk.TracerProvider()
span_otlp_exporter = OTLPSpanExporter(endpoint=endpoint)
tracer_provider.add_span_processor(SimpleSpanProcessor(span_exporter=span_otlp_exporter))

trace_api.set_tracer_provider(tracer_provider=tracer_provider)
DSPyInstrumentor().instrument()

## 📚 DSPy Module Definitions

If you're new to DSPy, check out this [DSPy Cookbook💻](https://colab.research.google.com/drive/1Y3TBXerpGZkzW-BhmyroWJBaG5tuadRP).

1. Define Entities (to annotate)
2. Define DSPy Annotation Program
3. Compile DSPy Programs
4. Functions to execute and aggregate annotations


In [ ]:
#@title New Entities with Definitions and Examples

#@markdown We define our entities (and 4 examples for each), to be included in the signature (prompt).

#@markdown Here we load them into a list of DSPy Example() classes, to later be compiled with the module.

import pandas as pd

################################## GENERALIZATION #######################################

GEN_entity_tag = "B-GEN/I-GEN"
GEN_entity_description = "GEN (generalizations), any broad generalization of a group or ubiquitous classifiers, including adjectives/descriptors (e.g., 'my whole family', 'all Muslims', 'Women in general', 'everyone in this city', 'all politicians',  'tall people', 'women', 'the rocketry club', 'students', 'tall boys')"
GEN_examples = {
    "input_str": [
        "Women are all such bad drivers",
        "Everyone from the city is rude and unfriendly",
        "John is usually late to meetings",
        "The college students on my street are always so loud"
    ],
    "rationale": [
        "The use of the word 'women' in this broad statement is a generalization because it is not about any specific woman or group of women. The use of the words 'are' and 'all' is a ubiquitous classification, extending the generalization entity another two words.",
        "The phrase 'Everyone from the city' generalizes the behavior of all people from the city, which is a broad and unjustified assumption. The words 'is' and 'rude and unfriendly' extend this generalization.",
        "This phrase makes a statement about John's punctuality, but does it is specific to one person, and uses the word 'usually' which is a hedge and not a generalization.",
        "This phrase unfairly characterizes a large group of people (country people) as loud. The use of the word 'always' is a ubiquitious classifier, therefore this contains a generalization."
    ],
    "annotations": [
        "['B-GEN', 'I-GEN', 'I-GEN', 'O', 'O', 'O']",
        "['B-GEN', 'I-GEN', 'I-GEN', 'I-GEN', 'O', 'O', 'O']",
        "['O', 'O', 'O', 'O', 'O', 'O', 'O']",
        "['O', 'B-GEN', 'I-GEN', 'I- GEN', 'I-GEN', 'I-GEN', 'I-GEN', 'O', 'O']"
    ]
}
GEN_df = pd.DataFrame(GEN_examples)
GEN_dataset = []
for input_str, rationale, annotations in GEN_df.values:
      input_str_len = str(len(input_str.split(" ")))
      GEN_dataset.append(dspy.Example(given_entity_tag=GEN_entity_tag, given_entity_description=GEN_entity_description, input_str=input_str, str_len=input_str_len, rationale=rationale, annotations=annotations).with_inputs("given_entity_tag", "given_entity_description", "input_str"))
print(GEN_dataset)


################################## UNFAIRNESS #######################################

UNFAIR_entity_tag = "B-UNFAIR/I-UNFAIR"
UNFAIR_entity_description = "UNFAIR (unfairness), any harsh or unjust characterization or offensive language. (e.g., 'such an idiot', 'stupid idea', 'totally useless', 'worst team ever', 'bad driver')"
UNFAIR_examples = {
    "input_str": [
        "Women are all such bad drivers",
        "Your golf swing is terrible",
        "That guy can be a real asshole",
        "You might want to work on your public speaking"
    ],
    "rationale": [
        "This statement unfairly generalizes about all women, making an unjustified claim about their driving skills. The words 'are all such' contribute to the severity of the unfair generalization.",
        "This statement unfairly criticizes someone's golf swing without constructive feedback, making it a negative and unhelpful comment. The word 'terrible' is particularly harsh and contributes to the unfairness.",
        "This statement unfairly labels someone as an 'asshole' without providing context or justification, making it an unwarranted and harsh characterization. The use of 'a real' intensifies the offensive nature of the comment.",
        "This statement offers a suggestion for improvement rather than an unjustified negative characterization, so it does not contain unreasonable unfariness/offensiveness."
    ],
    "annotations": [
        "['O', 'O', 'B-UNFAIR', 'I-UNFAIR', 'I-UNFAIR', 'I-UNFAIR']",
        "['O', 'O', 'O', 'O', 'B-UNFAIR']",
        "['O', 'O', 'O', 'O', 'B-UNFAIR', 'I-UNFAIR', 'I-UNFAIR']",
        "['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O']"
    ]
}
UNFAIR_df = pd.DataFrame(UNFAIR_examples)
UNFAIR_dataset = []
for input_str, rationale, annotations in UNFAIR_df.values:
      input_str_len = str(len(input_str.split(" ")))
      UNFAIR_dataset.append(dspy.Example(given_entity_tag=UNFAIR_entity_tag, given_entity_description=UNFAIR_entity_description, input_str=input_str, str_len=input_str_len, rationale=rationale, annotations=annotations).with_inputs("given_entity_tag", "given_entity_description", "input_str"))
print(UNFAIR_dataset)


################################## STEREOTYPE #######################################

STEREO_entity_tag = "B-STEREO/I-STEREO"
STEREO_entity_description = "STEREO (stereotypes), any statement (multiple words) that contain a stereotype targeting a group of people, both explicitly and unconsiously. (e.g., 'women are bad drivers', 'Asians are good at math', 'Sou ioutils are dumb', 'teenagers are irresponsible', 'men are gross')."
STEREO_examples = {
    "input_str": [
        "Women are all such bad drivers",
        "He's probably good at math because he's Asian",
        "White people don't know how to season their food, except for my one friend. Besides that, all their food tastes like chalk.",
        "I heard she's really mean to her teammates."
    ],
    "rationale": [
        "This statement perpetuates a stereotype that women are bad drivers, unfairly generalizing the driving skills of all women.",
        "This statement perpetuates a stereotype that all Asians are good at math, which is a broad and unfair assumption based on ethnicity.",
        "This statement perpetuates a stereotype that white people cannot cook or season their food well. It contains multiple stereotypical assertions about an entire group, with a brief exception that does not mitigate the overall stereotype.",
        "This statement does not contain a stereotype as it refers to an individual's behavior rather than making a broad generalization about a group."
    ],
    "annotations": [
        "['B-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO']",
        "['O', 'O', 'B-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO']",
        "['B-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO', 'I-STEREO']",
        "['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O']"
    ]
}
STEREO_df = pd.DataFrame(STEREO_examples)
STEREO_dataset = []
for input_str, rationale, annotations in STEREO_df.values:
      input_str_len = str(len(input_str.split(" ")))
      STEREO_dataset.append(dspy.Example(given_entity_tag=STEREO_entity_tag, given_entity_description=STEREO_entity_description, input_str=input_str, str_len=input_str_len, rationale=rationale, annotations=annotations).with_inputs("given_entity_tag", "given_entity_description", "input_str"))
print(STEREO_dataset)

[Example({'given_entity_tag': 'B-GEN/I-GEN', 'given_entity_description': "GEN (generalizations), any broad generalization of a group or ubiquitous classifiers, including adjectives/descriptors (e.g., 'my whole family', 'all Muslims', 'Women in general', 'everyone in this city', 'all politicians',  'tall people', 'women', 'the rocketry club', 'students', 'tall boys')", 'input_str': 'Women are all such bad drivers', 'str_len': '6', 'rationale': "The use of the word 'women' in this broad statement is a generalization because it is not about any specific woman or group of women. The use of the words 'are' and 'all' is a ubiquitous classification, extending the generalization entity another two words.", 'annotations': "['B-GEN', 'I-GEN', 'I-GEN', 'O', 'O', 'O']"}) (input_keys={'given_entity_tag', 'input_str', 'given_entity_description'}), Example({'given_entity_tag': 'B-GEN/I-GEN', 'given_entity_description': "GEN (generalizations), any broad generalization of a group or ubiquitous classifi

In [ ]:
#@title Individual Entity Annotation DSPy Module

#@markdown We define module for annotating a sentence with *one* entity. It can be reused for many entities, provided a definition.

###########################################################################################
from dspy.primitives.assertions import assert_transform_module, backtrack_handler
from dspy import Suggest
import ast
import json

class NERIndividualAnnotationModule(dspy.Module):
    class NERIndividualAnnotationSignature(dspy.Signature):
        """
        Your job is to take a sentence, and return a list of NER labels (one for each word in the sentence).

        Analyze each word of an entire sentence for NER labelling of your given entity. If any of the words in the sentence contain this given part-of-speech, it should be labeled.
        Identify where, if at all, the entity should be labeled on the sentence, using BIO format:
          B- prefix indicates the beginning of an entity.
          I- prefix indicates the inside of an entity.
          O indicates a token outside any entity.
          Every word should have exactly one entity tag.
          BIO format example: input string: "Word1 word2 word3", Reasoning: "one sentence analysis of word1, one sentence analysis of word2, one sentence analysis of word3" -> annotations: ["B-ABC", "I-ABC", "O"].
        If the given entity is not relevant to the word or sentence in question, it should be labeled with "O".

        Also check that all entities are continuous (an O tag cannot be followed by an I tag).
        """
        # entity info
        given_entity_tag = dspy.InputField(desc="The given entity for NER labeling.")
        given_entity_description = dspy.InputField(desc="A description of how/when a word should be labeled with the given entity.")
        # input info
        input_str = dspy.InputField(desc="The text string to analyze for the presence of the given entity.")
        str_len= dspy.InputField(desc="The number of words in the input string, aka the number of tags in the output list")
        rationale = dspy.OutputField(desc="The resasoning behind each entity assigned to each word.")
        # outputs
        annotations = dspy.OutputField(desc="List of labels of the entities in the input string. Entity bank: 'B-ABC', 'I-ABC', 'O'. Format this as a string: '['B-ABC', 'I-ABC', 'O']' ")

    def __init__(self, entity_tag, entity_description):
        self.annotate = dspy.TypedPredictor(self.NERIndividualAnnotationSignature)
        self.entity_tag = entity_tag
        self.entity_description = entity_description

    def forward(self, input_str):
        input_str_len = len(input_str.split())

        annotation_pred_obj = self.annotate(
            given_entity_tag=self.entity_tag,
            given_entity_description=self.entity_description,
            input_str=input_str,
            str_len=str(input_str_len)
            )
        # print(annotation_pred_obj)

        annotations_list = self._extract_list_from_str(annotation_pred_obj.annotations)

        Suggest(len(annotations_list) == input_str_len,
                f"The length of the annotation list should be {input_str_len}."
                )

        return annotations_list, annotation_pred_obj

    def _extract_list_from_str(self, string):
        # slice out the list in string form
        first_bracket_pos = string.find('[')
        last_bracket_pos = string.rfind(']') + 1
        annotations_str = string[first_bracket_pos:last_bracket_pos]

        try:
            annotations_list = ast.literal_eval(str(annotations_str))
        except Exception as e:
            print("Error extracting list from string:", string, e)
            annotations_list = annotations_str

        return annotations_list


# # example usage
# ner_annotator_agent = assert_transform_module(NERAnnotationModule(model=default_model), backtrack_handler)
# gen_annotator_agent = NERIndividualAnnotationModule(
#     entity_tag=GEN_entity_tag,
#     entity_description=GEN_entity_description,
#     )

# input_str = "Short people are always so loud" #@param
# final_pred = gen_annotator_agent(input_str=input_str)
# print("\n ======= Annotations: ======== \n\n", json.dumps(final_pred, indent=4))


In [ ]:
#@title Compile Modules for Each Entity

#@markdown We define modules for each of our entities, then "compile" them with DSPy LabeledFewShot, to include our examples directly in the signature.

#@markdown It's worth noting this isn't the intended use of DSPy, which would potentially create those examples without our manual definitions.

########################################################################################
from dspy.teleprompt import LabeledFewShot
from dspy.primitives.assertions import assert_transform_module, backtrack_handler

# define all agents
GEN_annotator_agent = NERIndividualAnnotationModule(
    entity_tag=GEN_entity_tag,
    entity_description=GEN_entity_description,
    )

UNFAIR_annotator_agent = NERIndividualAnnotationModule(
    entity_tag=UNFAIR_entity_tag,
    entity_description=UNFAIR_entity_description,
    )

STEREO_annotator_agent = NERIndividualAnnotationModule(
    entity_tag=STEREO_entity_tag,
    entity_description=STEREO_entity_description,
    )

# define the teleprompter/optimizer
teleprompter = LabeledFewShot(k=4)

# compile them with labeled fewshot and training sets
compiled_GEN_annotator_agent = teleprompter.compile(
    student=GEN_annotator_agent,
    trainset=GEN_dataset,
    )
compiled_GEN_annotator_agent = assert_transform_module(compiled_GEN_annotator_agent, backtrack_handler)

compiled_UNFAIR_annotator_agent = teleprompter.compile(
    student=UNFAIR_annotator_agent,
    trainset=UNFAIR_dataset,
    )
compiled_UNFAIR_annotator_agent = assert_transform_module(compiled_UNFAIR_annotator_agent, backtrack_handler)

compiled_STEREO_annotator_agent = teleprompter.compile(
    student=STEREO_annotator_agent,
    trainset=STEREO_dataset,
    )
compiled_STEREO_annotator_agent = assert_transform_module(compiled_STEREO_annotator_agent, backtrack_handler)

# example
# annotations = compiled_GEN_annotator_agent(input_str="I hate talking to old people, they're so slow")
# print("\n ======= Annotations: ======== \n\n", json.dumps(annotations, indent=4))
# default_model.inspect_history(1)

In [ ]:
#@title Functions to Run Annotation + Aggregate Annotations

##############################################################################

def annotate_ner_multi_label(input_str):
    # annotate with an agent for each entity
    GEN_annotations_list, GEN_pred_obj = compiled_GEN_annotator_agent(input_str=input_str)
    UNFAIR_annotations_list, UNFAIR_pred_obj = compiled_UNFAIR_annotator_agent(input_str=input_str)
    STEREO_annotations_list, STEREO_pred_obj = compiled_STEREO_annotator_agent(input_str=input_str)

    rationales_list = [GEN_pred_obj['rationale'], UNFAIR_pred_obj['rationale'], STEREO_pred_obj['rationale']]
    all_pred_objs = [GEN_pred_obj, UNFAIR_pred_obj, STEREO_pred_obj]

    annotations_list = []
    annotations_list.append(GEN_annotations_list)
    annotations_list.append(UNFAIR_annotations_list)
    annotations_list.append(STEREO_annotations_list)

    # return dict
    annotation = {}
    annotation['input_str'] = input_str
    annotation['ner_tags'] = aggregate_annotations_multi_label(annotations_list)
    annotation['rationale'] = str(rationales_list)
    annotation['individual_annotations'] = all_pred_objs

    return annotation

def aggregate_annotations_multi_label(annotations_list):
    # Find the maximum length among all annotation lists
    max_len = max(len(annotations) for annotations in annotations_list)

    # Initialize the merged_annotations list with 'O' for the maximum length
    merged_annotations = [['O'] for _ in range(max_len)]

    # Iterate over each annotation list
    for entity_annotations in annotations_list:
        for i in range(len(entity_annotations)):
            if entity_annotations[i] != 'O':
                if merged_annotations[i] == ['O']:
                    merged_annotations[i] = [entity_annotations[i]]
                else:
                    merged_annotations[i].append(entity_annotations[i])

    return merged_annotations

## 🤖 Run Annotations

In [ ]:
#@title NER Annotation Loop
from IPython.display import display, clear_output
import pandas as pd

# dataset was defined when we loaded babe
for index, row in dataset.iterrows():
    try:
        input_str = row['text']
        annotation = annotate_ner_multi_label(input_str)

        text_str = annotation['input_str']
        # print(len(input_str.split()))
        ner_tags = annotation['ner_tags']
        # print(len(ner_tags))
        rationale = annotation['rationale']
        ner_tags_str = str(ner_tags)
    except Exception as e:
        print(f"Error processing input str: {str(e)}")
        continue

    try:
        #### SAVE THE input_str, ner_tags, and rationale here (DB or CSV) ####

        # just for displaying
        tokens = input_str.split()
        data = {
            "Token": tokens,
            "NER Tags": [' '.join(tags) for tags in ner_tags]
        }
        df = pd.DataFrame(data)

        # clear_output(wait=True)
        display(df)

        # print(result)
        print(f"Annotated input str: {row['id']}, and inserted to db")

    except Exception as e:
        print(f"Error adding to db: {str(e)}")


Token NER Tags
0           NYPD        O
1   Commissioner        O
2         Dermot        O
3           Shea        O
4             on        O
5         Monday        O
6      expressed        O
7        support        O
8            for        O
9      diverting        O
10         funds        O
11          away        O
12          from        O
13           the        O
14        police        O
15    department        O
16           and        O
17            to        O
18         other    B-GEN
19        areas,    I-GEN
20          like        O
21         youth    B-GEN
22     programs.    I-GEN

Record added successfully
Error adding to db: 'id'


Token        NER Tags
0           School           B-GEN
1          systems           I-GEN
2           across               O
3              the               O
4          country           B-GEN
5              are               O
6         adopting               O
7              BLM               O
8       curriculum               O
9               at               O
10              at               O
11        alarming               O
12           rate,               O
13  indoctrinating        B-UNFAIR
14             our        I-UNFAIR
15        children        I-UNFAIR
16              to  B-GEN I-UNFAIR
17         achieve        I-UNFAIR
18         Marxist        I-UNFAIR
19     objectives.        I-UNFAIR

Record added successfully
Error adding to db: 'id'


Token  NER Tags
0         And         O
1        then         O
2       along         O
3        came         O
4   President         O
5       Barry         O
6      Obama,         O
7         who         O
8       spent         O
9   trillions         O
10         of         O
11    dollars         O
12         on         O
13          —         O
14       what  B-UNFAIR
15        the  I-UNFAIR
16       hell  I-UNFAIR
17        did         O
18         he         O
19      spend         O
20        all     B-GEN
21       that     I-GEN
22      money     I-GEN
23        on?         O

...

Record added successfully
Error adding to db: 'id'


Token NER Tags
0         WILL        O
1        noted        O
2       gender        O
3    dysphoria        O
4           is        O
5            a        O
6       mental        O
7       health        O
8        issue        O
9          and        O
10     parents    B-GEN
11        have        O
12         the        O
13       right        O
14          to        O
15        make        O
16  healthcare        O
17   decisions        O
18          on        O
19      behalf        O
20          of        O
21       their        O
22   children.    B-GEN

Record added successfully
Error adding to db: 'id'


Token NER Tags
0          H.R.7        O
1           bans        O
2        private        O
3      insurance        O
4      companies        O
5           from        O
6       offering        O
7       abortion        O
8       coverage        O
9             to        O
10      American    B-GEN
11     consumers    I-GEN
12       through        O
13           the        O
14    Affordable        O
15          Care        O
16           Act        O
17  marketplace.        O

Record added successfully
Error adding to db: 'id'
Error adding to db: All arrays must be of the same length
Error adding to db: All arrays must be of the same length
